## CS 132 Homework 03 A  


### Due Wednesday July 28th at Midnight (1 minute after 11:59pm) in Gradescope (with grace period of 6 hours)
### Homeworks may be submitted up to 24 hours late with a 10% penalty (same grace period)

### Homework 03 B will be posted Friday before lecture


Please read through the entire notebook, reading the expository material and then do the problems, following the instuctions to try various features; among the exposition of various features of Python there
are three problems which will be graded.  The homework is worth 30 points. 

You will need to complete this notebook and then convert to a PDF file in order to submit to Gradescope. Instructions are given here:

https://www.cs.bu.edu/fac/snyder/cs132/HWSubmissionInstructions.html



In [20]:
# Here are some imports which will be used in the code in the rest of the lab  

# Imports used for the code in CS 237

import numpy as np                # arrays and functions which operate on arrays

import matplotlib.pyplot as plt   # normal plotting


# NOTE: You may not use any other libraries than those listed here without explicit permission.

## Preface to Lab Problems

The following cell contains an implementation of the Gaussian Elimination code we have developed
in the last two weeks. Please read through the comments to understand how to use the various functions

In [21]:
# Gaussian Elimination

# number of digits of precision to print out

prec = 4

########################################################################################################

# Returns the Row Echelon (upper triangular) form

def forwardElimination(A,traceLevel=0):
    
    A = (np.copy(A)).astype(float)
    
    if (traceLevel > 0):
        print("Running Forward Elimination on:\n")
        print(np.round(A, decimals=4),"\n")
        print()
    
    (numRows,numCols) = A.shape
    
    # r = row we are currently working on         pivot value is A[r][c]
    r = 0            
    for c in range(numCols):     # solve for variable in column c 
        # find row in column c with first non-zero element, and exchange with row r                  
        r1 = r
        while(r1 < numRows):
            if (not np.isclose(A[r1][c],0.0)):   # A[r1][c] is first non-zero element at or below r in column c
                break
            r1 += 1
        
        if(r1 == numRows):    # all zeros below r in this column
            continue          # go on to the next column, but still working on same row   
         
        if(r1 != r): 
            # exchange rows r1 and r
            A[[r1,r],:] = A[[r,r1],:] 
            if (traceLevel == 2): 
                print("Exchange R" + str(r1+1) + " and R" + str(r+1) + "\n") 
                print(np.round(A, decimals=4))                
                print() 

        # now use pivot A[r][c] to eliminate all vars in this column below row r
        for r2 in range(r+1,numRows):
            rowReduce(A,r,c,r2,traceLevel)
            
        r += 1  
        if (r >= numRows):
            break
            
    return A

# for pivot A[r][c], eliminate variable in location A[r2][c] in row r2 using row operations

def rowReduce(A,r,c,r2,traceLevel=0):

    if(not np.isclose(A[r2][c],0.0)):

        factor = -A[r2][c]/A[r][c] 
        A[r2] += factor * A[r]
            
        if(traceLevel == 2):
            print("R" + str(r2+1) + " += " + str(np.around(factor,prec)) + "*R" + str(r+1) + "\n")  
            print(np.round(A, decimals=4))
            print()

# Take a Row Echelon Form and return a Reduced Row Echelon Form

def backwardSubstitute(A,augmented=True,traceLevel=0): 
    
    numRows,numCols = A.shape
    
    if (A.dtype != 'float64'):
        A = A.astype(float)

    # now back-substitute the variables from bottom row to top
    if (traceLevel > 0):
        print("Creating Reduced Row Echelon Form...\n") 

    for r in range(numRows):

        # find variable in this row
        for c in range(numCols):
            if(not np.isclose(A[r][c],0.0)):
                break 
       
        if ((augmented and c >= numCols-1) or (c >= numCols)):        # inconsistent or redundant row
                continue 
                        
        # A[r][c] is variable to eliminate
        
        factor = A[r][c]
        
        if (np.isclose(factor,0.0)):   # already eliminated
            continue
        
        if(not np.isclose(factor,1.0)):  
            A[r] *= 1/factor
            if (traceLevel == 2):
                print("R" + str(r+1) + " = R" + str(r+1) + "/" + str(np.around(factor,prec)) + "\n")  
                print(np.round(A, decimals=4))
                print()

        for r2 in range(r): 
            rowReduce(A,r,c,r2,traceLevel)
            
    return A 

    
# try to find row of all zeros except for last column, in augmented matrix. 

def noSolution(A):
    numRows,numCols = A.shape
    for r in range(numRows-1,-1,-1):         # start from bottom, since inconsistent rows end up there
        for c in range(numCols):
            if(not np.isclose(A[r][c],0.0)):  # found first non-0 in this row
                if(c == numCols-1):
                    return True
                else:
                    break
    return False

########################################################################################################

# Runs GE and returns a reduced row echelon form

# If b == None assumes that A is NOT an augmented matrix, and runs GE and returns Reduced Row Echelon Form

# If b is a column matrix then adjoins it to A and runs GE;
#       Always returns the Reduced Row Echelon Form
#       If inconsistent then also prints out "Inconsistent!"

# If b is a length n array instead of a 1 x n array (column vector)
# b will be converted to a column vector, for convenience. 

# traceLevel 0 will not print anything out during the run
# traceLevel 1 will print out various stages of the process and the intermediate matrices
# traceLevel 2 will also print out the row operations used at each step. 

# If you want to produce an Echelon Form (NOT reduced), then use forwardElimination instead. 

# See examples for more explanation of how to use this

def GaussianElimination(A,b=None, traceLevel = 0):
    if( type(b) != type(None)):
        if( (A.shape)[0] == 1 ):
            b = np.array([b]).T
        Ab = (np.hstack((A.copy(),b))).astype(float)
    else:
        Ab = A.copy().astype(float)
        
    if( traceLevel > 0 and type(b) == type(None)):
        print("Creating Reduced Row Echelon Form:\n")
        print(np.round(Ab, decimals=4))
        print()
    elif( traceLevel > 0 ):
        print("Running Gaussian Elimination on augmented matrix:\n")
        print(np.round(Ab, decimals=4))
        print()
        
    B = forwardElimination(Ab,traceLevel)
    
    if( traceLevel > 0 ):
        print("Echelon Form:\n")
        print( np.round(B, decimals=4) + np.zeros(B.shape),"\n")       # adding -0.0 + 0 gives 0.0
        print()
        
    if ( type(b) != type(None) and noSolution(B) ):
        print("No solution!")

    C = backwardSubstitute(B,type(b)!=type(None),traceLevel)
        
    if( traceLevel > 0 ):
        print("Reduced Row Echelon Form:\n")
        print( np.round(C, decimals=4) + np.zeros(C.shape),"\n")   # adding -0.0 + 0 gives 0.0
        print()
            
    return C

########################################################################################################
  


In [22]:
# Using just forward elimination to generate a Row Echelon Form

A = np.array( [ [1,2,3],[4,5,6],[-3,8,10]])

forwardElimination(A)

array([[ 1.,  2.,  3.],
       [ 0., -3., -6.],
       [ 0.,  0., -9.]])

In [23]:
# See all the steps

forwardElimination(A,2)

Running Forward Elimination on:

[[ 1.  2.  3.]
 [ 4.  5.  6.]
 [-3.  8. 10.]] 


R2 += -4.0*R1

[[ 1.  2.  3.]
 [ 0. -3. -6.]
 [-3.  8. 10.]]

R3 += 3.0*R1

[[ 1.  2.  3.]
 [ 0. -3. -6.]
 [ 0. 14. 19.]]

R3 += 4.6667*R2

[[ 1.  2.  3.]
 [ 0. -3. -6.]
 [ 0.  0. -9.]]



array([[ 1.,  2.,  3.],
       [ 0., -3., -6.],
       [ 0.,  0., -9.]])

In [24]:
# Just find a RREF

GaussianElimination(A)

array([[ 1.,  0.,  0.],
       [ 0.,  1.,  0.],
       [-0., -0.,  1.]])

In [25]:
# Find a RREF and trace all the stages and row ops

GaussianElimination(A,traceLevel=2)

Creating Reduced Row Echelon Form:

[[ 1.  2.  3.]
 [ 4.  5.  6.]
 [-3.  8. 10.]]

Running Forward Elimination on:

[[ 1.  2.  3.]
 [ 4.  5.  6.]
 [-3.  8. 10.]] 


R2 += -4.0*R1

[[ 1.  2.  3.]
 [ 0. -3. -6.]
 [-3.  8. 10.]]

R3 += 3.0*R1

[[ 1.  2.  3.]
 [ 0. -3. -6.]
 [ 0. 14. 19.]]

R3 += 4.6667*R2

[[ 1.  2.  3.]
 [ 0. -3. -6.]
 [ 0.  0. -9.]]

Echelon Form:

[[ 1.  2.  3.]
 [ 0. -3. -6.]
 [ 0.  0. -9.]] 


Creating Reduced Row Echelon Form...

R2 = R2/-3.0

[[ 1.  2.  3.]
 [-0.  1.  2.]
 [ 0.  0. -9.]]

R1 += -2.0*R2

[[ 1.  0. -1.]
 [-0.  1.  2.]
 [ 0.  0. -9.]]

R3 = R3/-9.0

[[ 1.  0. -1.]
 [-0.  1.  2.]
 [-0. -0.  1.]]

R1 += 1.0*R3

[[ 1.  0.  0.]
 [-0.  1.  2.]
 [-0. -0.  1.]]

R2 += -2.0*R3

[[ 1.  0.  0.]
 [ 0.  1.  0.]
 [-0. -0.  1.]]

Reduced Row Echelon Form:

[[1. 0. 0.]
 [0. 1. 0.]
 [0. 0. 1.]] 




array([[ 1.,  0.,  0.],
       [ 0.,  1.,  0.],
       [-0., -0.,  1.]])

In [26]:
# if no solution....

A = np.array( [ [1,2,3],[4,5,6],[7,8,9]])
b = np.array( [[2],[1],[-1]] )

GaussianElimination(A,b)

No solution!


array([[ 1.        ,  0.        , -1.        , -2.66666667],
       [-0.        ,  1.        ,  2.        ,  2.33333333],
       [ 0.        ,  0.        ,  0.        , -1.        ]])

In [27]:
# Tracing the stages of the process 

A = np.array( [ [1,2,3],[4,5,6],[7,8,10]])
b = np.array( [[2],[1],[-1]])

GaussianElimination(A,b,1)

Running Gaussian Elimination on augmented matrix:

[[ 1.  2.  3.  2.]
 [ 4.  5.  6.  1.]
 [ 7.  8. 10. -1.]]

Running Forward Elimination on:

[[ 1.  2.  3.  2.]
 [ 4.  5.  6.  1.]
 [ 7.  8. 10. -1.]] 


Echelon Form:

[[ 1.  2.  3.  2.]
 [ 0. -3. -6. -7.]
 [ 0.  0.  1. -1.]] 


Creating Reduced Row Echelon Form...

Reduced Row Echelon Form:

[[ 1.      0.      0.     -3.6667]
 [ 0.      1.      0.      4.3333]
 [ 0.      0.      1.     -1.    ]] 




array([[ 1.        ,  0.        ,  0.        , -3.66666667],
       [-0.        ,  1.        ,  0.        ,  4.33333333],
       [ 0.        ,  0.        ,  1.        , -1.        ]])

In [28]:
# Tracing all the row ops

A = np.array( [ [1,2,3],[4,5,6],[7,8,10]])
b = np.array( [[2],[1],[-1]])

GaussianElimination(A,b,2)

Running Gaussian Elimination on augmented matrix:

[[ 1.  2.  3.  2.]
 [ 4.  5.  6.  1.]
 [ 7.  8. 10. -1.]]

Running Forward Elimination on:

[[ 1.  2.  3.  2.]
 [ 4.  5.  6.  1.]
 [ 7.  8. 10. -1.]] 


R2 += -4.0*R1

[[ 1.  2.  3.  2.]
 [ 0. -3. -6. -7.]
 [ 7.  8. 10. -1.]]

R3 += -7.0*R1

[[  1.   2.   3.   2.]
 [  0.  -3.  -6.  -7.]
 [  0.  -6. -11. -15.]]

R3 += -2.0*R2

[[ 1.  2.  3.  2.]
 [ 0. -3. -6. -7.]
 [ 0.  0.  1. -1.]]

Echelon Form:

[[ 1.  2.  3.  2.]
 [ 0. -3. -6. -7.]
 [ 0.  0.  1. -1.]] 


Creating Reduced Row Echelon Form...

R2 = R2/-3.0

[[ 1.      2.      3.      2.    ]
 [-0.      1.      2.      2.3333]
 [ 0.      0.      1.     -1.    ]]

R1 += -2.0*R2

[[ 1.      0.     -1.     -2.6667]
 [-0.      1.      2.      2.3333]
 [ 0.      0.      1.     -1.    ]]

R1 += 1.0*R3

[[ 1.      0.      0.     -3.6667]
 [-0.      1.      2.      2.3333]
 [ 0.      0.      1.     -1.    ]]

R2 += -2.0*R3

[[ 1.      0.      0.     -3.6667]
 [-0.      1.      0.      4.3333]

array([[ 1.        ,  0.        ,  0.        , -3.66666667],
       [-0.        ,  1.        ,  0.        ,  4.33333333],
       [ 0.        ,  0.        ,  1.        , -1.        ]])

### Ok, Your Turn!

In the following problems, you will analyze a matrix (NOT an augmented matrix) to calculate some useful information
about the matrix.

Before doing these problems, you should study the Numpy Tutorial posted in the tutorials directory on the class
web site, especially the later sections on Indexing and Slicing, Rearranging Rows and Columns, and Array Stacking. 

## Problem 1

In this problem, we will take a matrix $A$ and return a tuple consisting of the following information about $A$:

- The rank of A, i.e., the number of pivots
- A basis for the column space of A 
- The nullity of A, i.e., the number of free variables
- A basis for the null space of A

Examples of what your function should return are given in the following cells.  

Hint: Here are the steps your algorithm should follow:

- Calculate the RREF form of A;  call this B
- Use a double-for loop just as you did in HW 01 to find the pivot positions
- Collect together a list of the columns where pivots occur
- Calculate a list of non-pivot columns
- The basis for Col(A) is the columns in A where pivots occur in B
- The basis for Null(A) is -1 times the columns in B where pivots do NOT occur, with a 1 added at the position of
  the corresponding variable 
- Rank and nullity can be calculated from the size of the two bases. 

In [29]:
def analyzeMatrix(A):

    # Your code here
    
    return (None,None,None,None)     # just to get it to compile, replace with your code

    

### Testing Examples

To determine if your code is correct, calculate the bases by hand. 

In [30]:
# Example (A)

A = np.array( [ [1,2,3],[4,5,6],[7,8,9]])
print(A,'\n')
analyzeMatrix(A)

[[1 2 3]
 [4 5 6]
 [7 8 9]] 



(None, None, None, None)

In [31]:
# Example (B)

A = np.array( [ [1,2,3],[2,4,31],[3,2,10]])
print(A,'\n')
analyzeMatrix(A)

[[ 1  2  3]
 [ 2  4 31]
 [ 3  2 10]] 



(None, None, None, None)

In [32]:
# Example (C)

A = np.array( [ [1,2,3],[2,4,6],[3,6,9]])
print(A,'\n')
analyzeMatrix(A)

[[1 2 3]
 [2 4 6]
 [3 6 9]] 



(None, None, None, None)

## Problem 2

In this problem, we will take a matrix $A$ and calculate the inverse matrix $A^{-1}$, if it exists; if $A$ has
no inverse, you will return the value `None`. 

You should use the functions defined above, and the method shown on Friday for calculating the inverse
of a square matrix.

You may use the function `analyzeMatrix` created in the previous problem if you wish. 

In [33]:
# If A has no inverse (i.e., is not square or does not have a pivot in every row) then return None,
# else calculate the inverse by horizontally stacking the identity matrix, as shown in lecture on Friday 7/23

def getInverse(A):

    # Your code here
    
    return None    # just to get it to compile, replace with your code

In [34]:
# Example A

A = np.array( [ [1,2,3],[-2,4,3],[3,6,-9]])
print("A:")
print(A,'\n')
Ainv = getInverse(A)
print("Inverse:")
print(Ainv,'\n')

# Uncomment these to test your code

'''
print("Test Inverse:  A @ Ainv (without rounding) = ")
print(A @ Ainv,'\n')
print("Test Inverse:  A @ Ainv (with rounding) = ")
print(np.around(A @ Ainv),'\n')
print("Test Inverse:  Ainv @ A (with rounding) = ")
print(np.around(Ainv @ A),'\n')
print("Test Inverse:  A @ A @ A @ Ainv @ Ainv @ Ainv (with rounding) = ")
print(np.around(A @ A @ A @ Ainv @ Ainv @ Ainv),'\n')
'''
print()

A:
[[ 1  2  3]
 [-2  4  3]
 [ 3  6 -9]] 

Inverse:
None 




In [35]:
# Example B

A = np.array( [ [1,2,3,5,2],[-2,4,3,8,4],[3,6,-9,1,2],[2,8,3,8,0],[1,16,9,1,-2]])
print("A:")
print(A,'\n')
Ainv = getInverse(A)
print("Inverse:")
print(Ainv,'\n')

# Uncomment these to test your code

'''
print("Test Inverse:  A @ Ainv (without rounding) = ")
print(A @ Ainv,'\n')
print("Test Inverse:  A @ Ainv (with rounding) = ")
print(np.around(A @ Ainv),'\n')
print("Test Inverse:  Ainv @ A (with rounding) = ")
print(np.around(Ainv @ A),'\n')
print("Test Inverse:  A @ A @ A @ Ainv @ Ainv @ Ainv (with rounding) = ")
print(np.around(A @ A @ A @ Ainv @ Ainv @ Ainv),'\n')
'''
print()

A:
[[ 1  2  3  5  2]
 [-2  4  3  8  4]
 [ 3  6 -9  1  2]
 [ 2  8  3  8  0]
 [ 1 16  9  1 -2]] 

Inverse:
None 




In [36]:
# Example C

A = np.eye(10)
print("A:")
print(A,'\n')
Ainv = getInverse(A)
print("Inverse:")
print(Ainv,'\n')

# Uncomment these to test your code

'''
print("Test Inverse:  A @ Ainv (without rounding) = ")
print(A @ Ainv,'\n')
print("Test Inverse:  A @ Ainv (with rounding) = ")
print(np.around(A @ Ainv),'\n')
print("Test Inverse:  Ainv @ A (with rounding) = ")
print(np.around(Ainv @ A),'\n')
print("Test Inverse:  A @ A @ A @ Ainv @ Ainv @ Ainv (with rounding) = ")
print(np.around(A @ A @ A @ Ainv @ Ainv @ Ainv),'\n')
'''
print()

A:
[[1. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
 [0. 1. 0. 0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 1. 0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 1. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 1. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 1. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 1. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0. 1. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0. 0. 1. 0.]
 [0. 0. 0. 0. 0. 0. 0. 0. 0. 1.]] 

Inverse:
None 




In [37]:
# Example D

A = np.array( [ [1,2,3],[4,5,6],[7,8,9]])
print("A:")
print(A,'\n')
Ainv = getInverse(A)
print("Inverse:")
print(Ainv,'\n')                # Should print None


A:
[[1 2 3]
 [4 5 6]
 [7 8 9]] 

Inverse:
None 



### Problem 3

Solve these problems using Python/numpy. One goal of these problems is to make you more
familiar with using the numpy documentation. It is available at 

      http://docs.scipy.org/doc/numpy/reference/index.html. 
      
Parts of the documentation you will want to read include array creation routines, random
number generation routines, and mathematical functions (for rounding).  You should also look over
my `numpy` tutorial on the web site. 

To generate random matrices, you will want to use the `numpy.random` package. (Python has a stand-alone
random library as well, but it will be easier for you if you use routines in numpy.random, so use that library in
your answers below).

(A) For each case, determine the call to a numpy function that will produce the stated matrix. Show an example in a code cell. 

1. A $5\times 6$ matrix of all zeros. 

2. A $3\times 5$ matrix of all ones. 

3. The $6\times 6$ identity matrix.

4. A $5\times 5$ diagonal matrix, with diagonal entries 3, 5, 7, 2, 4. 

(B) Write an expression which will create a $6\times 4$ matrix containing random floating-point numbers. Show an example in a code cell. 

(C) The expression in (B) created all numbers in the range $[0,1)$; write an expression which would create a random $5\times 5$ matrix with floating-point numbers in the range $[100,200)$. Show an example in a code cell. 



In [38]:
# Solution



### Problem 4

Construct a random $4\times 4$ matrix and test whether the following equality holds:

$$(A+I_4)(A-I_4) = (A^2 - I_4).$$

The best way to do this is to compute the difference between the two sides of the equation
and see if it contains all zeros -- however, you will have to use the function `np.isclose(...)`
because of the problems with floating-point arithmetic. 


Provide your code, run it, and state whether the equation holds. 
